## Notebook Description

This is an implementation of instantaneous pulse rate estimation algorithm described in:
> Xu, Ke, et al. "Deep Recurrent Neural Network for Extracting Pulse Rate Variability from Photoplethysmography During Strenuous Physical Exercise." 2019 IEEE Biomedical Circuits and Systems Conference (BioCAS). IEEE, 2019.

The dataset comes from the author's [github](https://github.com/WillionXU/CIME-PPG-dataset-2018/).

In [48]:
from pathlib import Path

import numpy as np
import pandas as pd
import plotly.graph_objects as go

from plotly.subplots import make_subplots
from scipy import io as sci_io
from tqdm import tqdm


DATA_PATH = Path('/Volumes/Samsung_SSD/CIME-PPG-dataset-2018')

## Prepare Data

In [2]:
train_all_noise = sci_io.loadmat(DATA_PATH / 'train_all_noise.mat')
test_all_noise = sci_io.loadmat(DATA_PATH / 'test_all_noise.mat')

In [3]:
train_all_noise.keys()

dict_keys(['__header__', '__version__', '__globals__', 'noise_input_all', 'noise_output_all'])

In [4]:
train_input = train_all_noise['noise_input_all']
train_output = train_all_noise['noise_output_all']
test_input = test_all_noise['noise_input_all']
test_output = test_all_noise['noise_output_all']

### Dataset Description

In [5]:
print(f'{train_input.shape=}, {train_output.shape=}, {test_input.shape=}, {test_output.shape=}')

train_input.shape=(5, 1000), train_output.shape=(5, 1000), test_input.shape=(5, 380), test_output.shape=(5, 380)


According to the author's description, the dataset is organized as following:
For training and testing dataset with shape (5, 1000) or (5, 380), each element represent for a 30 sec of data in Matlab cell matrix format, and each column with 5 elements represents for 1 sequence. The sequence-wise concatenation is doable, thus will give you a 30 * 5 = 150 sec data.

For the **input data (X)**, each Matlab cell matrix contains 30 sec * 3 rows of signals, which are corrupted PPG in the 1st row, x-axis accelerometer in the 2nd row and y-axis gyroscope in the 3rd row.

For the **output data (y)**, each Matlab cell matrix contains 30 sec * 1 row of signal, which is the clean PPG.

Sensor sampling frequency is 200 Hz, but further down-sampled to 100 Hz in this dataset.

For more details, please refer to [data description page](https://github.com/WillionXU/CIME-PPG-dataset-2018/blob/master/dataset_description.pdf).



### Visualize a signal sequence in training set.

In [21]:
visualize_seq_input = train_input[:, 0]
visualize_seq_output = train_output[:, 0]

corrupted_ppg = []
x_acce = []
y_gyro = []
clean_ppg = []

for _input, _output in zip(visualize_seq_input, visualize_seq_output):
    corrupted_ppg.extend(_input[0].tolist())
    x_acce.extend(_input[1].tolist())
    y_gyro.extend(_input[2].tolist())
    clean_ppg.extend(_output[0].tolist())
    
# The PPG signal is usually flipped to visualize
corrupted_ppg = np.array(corrupted_ppg)
clean_ppg = np.array(clean_ppg)
corrupted_ppg = 2 * corrupted_ppg.mean() - corrupted_ppg
clean_ppg = 2 * clean_ppg.mean() - clean_ppg

def visualize_seq(_corrupted_ppg, _clean_ppg, _x_acce, _y_gyro):
    fig_seq = make_subplots(specs=[[{}], [{'secondary_y': True}]], rows=2, 
                            shared_xaxes=True, vertical_spacing=0.02)
    fig_seq.add_trace(go.Scatter(y=_corrupted_ppg, name='corrupted_ppg'), col=1, row=1)
    fig_seq.add_trace(go.Scatter(y=_clean_ppg, name='clean_ppg'), col=1, row=1)
    fig_seq.add_trace(go.Scatter(y=_x_acce, name='x_acce'), col=1, row=2)
    fig_seq.add_trace(go.Scatter(y=_y_gyro, name='y_gyro'), col=1, row=2, secondary_y=True)
    
    return fig_seq

visualize_seq(corrupted_ppg, clean_ppg, x_acce, y_gyro).show()

## Data Pre-processing

### Determine a 6 Hz cutoff low-pass FIR filter with Kaiser window

In [16]:
from scipy import signal as sci_signal

cutoff = 6    # in Hz
fir_ripple = 40    # upper bound of filter ripple, in dB
fir_width = 0.2    # width of transition region, in Hz
fs = 100

num_taps, beta = sci_signal.kaiserord(ripple=40, width=0.5/(0.5*fs))
taps = sci_signal.firwin(num_taps, cutoff, window=('kaiser', beta), fs=fs, pass_zero='lowpass')
print(f'FIR filter length = {num_taps}')

# Visualize the FIR filter frequency response.

w, h = sci_signal.freqz(taps, worN=8000)
plot_w = w * 0.5*fs / np.pi
plot_h_amplitude = 20 * np.log10(abs(h))

fig_fir = go.Figure()
fig_fir.add_trace(go.Scatter(x=plot_w, y=plot_h_amplitude))
fig_fir.update_layout(width=700, height=700).show()


FIR filter length = 448


### Determine and visualize the performance of the envelope filter

The enveloper filter is with the following equation.
$$x_{EF}=\frac{x(t)-e_{lower}(t)}{e_{upper}(t)-e_{lower}(t)}-0.5$$
$x_{EF}$ is the filterd signal, while $e_{upper}(t)$ and $e_{upper}(t)$ are the upper and lower envelopes respectively.

In [38]:
from scipy import interpolate as sci_interpolate

def envelope_filter(ppg_sig, fs, ret_peak_onsets=False):
    peaks_idx = sci_signal.find_peaks(ppg_sig, distance=fs//2)[0]
    onsets_idx = sci_signal.find_peaks(-ppg_sig, distance=fs//2)[0]
    assert len(peaks_idx) >= 5
    assert len(onsets_idx) >= 5
    
    upper_envelope = sci_interpolate.InterpolatedUnivariateSpline(x=peaks_idx, y=ppg_sig[peaks_idx], k=5)
    lower_envelope = sci_interpolate.InterpolatedUnivariateSpline(x=onsets_idx, y=ppg_sig[onsets_idx], k=5)
    
    eval_x_idx = np.arange(len(ppg_sig))
    ppg_ef = ((ppg_sig - lower_envelope(eval_x_idx)) / 
              (upper_envelope(eval_x_idx) - lower_envelope(eval_x_idx)) - 0.5)
    
    if ret_peak_onsets:
        return ppg_ef, peaks_idx, onsets_idx
    else:
        return ppg_ef


In [41]:
example_ppg = clean_ppg
example_ppg_ef, peaks_idx, onsets_idx = envelope_filter(example_ppg, fs=100, ret_peak_onsets=True)

fig_env = make_subplots(rows=2, shared_xaxes=True, vertical_spacing=0.02)
fig_env.add_trace(go.Scatter(y=example_ppg, name='ppg'), col=1, row=1)
fig_env.add_trace(go.Scatter(x=peaks_idx, y=example_ppg[peaks_idx], name='peaks', 
                             mode='lines+markers', marker=dict(symbol='triangle-up')))
fig_env.add_trace(go.Scatter(x=onsets_idx, y=example_ppg[onsets_idx], name='onsets', 
                             mode='lines+markers', marker=dict(symbol='triangle-down')))
fig_env.add_trace(go.Scatter(y=example_ppg_ef, name='ppg_envelope_filtered'), col=1, row=2)

### Pre-process PPG, ACCE, GYRO signals

Detrend and apply the low-pass FIR filter to the PPG, ACCE and GYRO signals; Apply envelope filter to the PPG signal.

In [52]:
def pre_process(signal_cell):
    processed_signal_list = []
    for i, sig in enumerate(signal_cell):
        detrended_sig = sig.mean() - sig
        filtered_sig = sci_signal.filtfilt(taps, 1, detrended_sig)
        if i == 0:
            filtered_sig = envelope_filter(filtered_sig, fs=fs, ret_peak_onsets=False)
        processed_signal_list.append(filtered_sig)
    
    return processed_signal_list
        

train_input_processed = []
for _cell in tqdm(train_input.flatten()):
    train_input_processed.append(pre_process(_cell))

test_input_processed = []
for _cell in tqdm(test_input.flatten()):
    test_input_processed.append(pre_process(_cell))
    
train_output_processed = []
for _cell in tqdm(train_output.flatten()):
    train_output_processed.append(pre_process(_cell))

test_output_processed = []
for _cell in tqdm(test_output.flatten()):
    test_output_processed.append(pre_process(_cell))        

100%|██████████| 1900/1900 [00:14<00:00, 127.32it/s]


In [53]:
# Save pre-processed dataset to outer storage
np.save(DATA_PATH / 'train_input_processed.npy', np.array(train_input_processed))
np.save(DATA_PATH / 'test_input_processed.npy', np.array(test_input_processed))
np.save(DATA_PATH / 'train_output_processed.npy', np.array(train_output_processed))
np.save(DATA_PATH / 'test_output_processed.npy', np.array(test_output_processed))